In [1]:
from ngsolve import *
from netgen.occ import *
from ngsolve.webgui import Draw
import matplotlib.pyplot as plt
from netgen.geom2d import SplineGeometry
import numpy as np
from ngsolve.nonlinearsolvers import Newton

In [2]:

maxH = 0.05
geo = OCCGeometry(Circle((0, 0), 0.9).Face(), dim=2).GenerateMesh(maxh=maxH)
mesh = Mesh(geo)

vol = 3e-2

a = 0.6
b = 0.4

ud = 1 - ((x-0.01)**2/a**2 + (y-0.01)**2/b**2)

f = (2/a**2 + 2/b**2) + ud

grad_f = CoefficientFunction( (f.Diff(x), f.Diff(y) ) )
grad_ud = CoefficientFunction( (ud.Diff(x), ud.Diff(y) ) )

#Draw(ud, mesh, "target_function")


In [3]:
fes = H1(mesh, order=2, dirichlet=".*")
u, v = fes.TnT()
gfu = GridFunction(fes)
scene_gfu = Draw (gfu, mesh, "state")

a = BilinearForm(fes, symmetric=True)
a += grad(u)*grad(v)*dx
a += u*v*dx

fstate = LinearForm(fes)
fstate += f*v*dx

WebGuiWidget(layout=Layout(height='50vh', width='100%'), value={'gui_settings': {}, 'ngsolve_version': '6.2.24…

In [4]:
def SolveStateEquation():
    rhs = gfu.vec.CreateVector()
    rhs.data = fstate.vec - a.mat * gfu.vec
    update = gfu.vec.CreateVector()
    update.data = a.mat.Inverse(fes.FreeDofs()) * rhs
    gfu.vec.data += update

In [5]:
a.Assemble()
fstate.Assemble()
SolveStateEquation()
scene_gfu.Redraw()

In [6]:
def Cost(u):
    cost = InnerProduct(grad(u) - grad_ud, grad(u) - grad_ud) * dx
    cost += InnerProduct(CF(vol), CF(1)) * dx

    return cost



p, w = fes.TnT()
gfp = GridFunction(fes)
scene_gfp = Draw (gfp, mesh, "adjoint")

fadjoint = LinearForm(fes)
#fadjoint += -1*Cost(gfu).Diff(gfu,w)
fadjoint += -2* InnerProduct(grad(gfu) - grad_ud, grad(w)) * dx

WebGuiWidget(layout=Layout(height='50vh', width='100%'), value={'gui_settings': {}, 'ngsolve_version': '6.2.24…

In [7]:
def SolveAdjointEquation():
    rhs = gfp.vec.CreateVector()
    rhs.data = fadjoint.vec - a.mat.T * gfp.vec
    update = gfp.vec.CreateVector()
    update.data = a.mat.Inverse(fes.FreeDofs()).T * rhs
    gfp.vec.data += update

In [8]:
fadjoint.Assemble()
SolveAdjointEquation()
scene_gfp.Redraw()

In [9]:
def hesse(u):
    return CoefficientFunction(
        (u.Diff(x).Diff(x), u.Diff(x).Diff(y),
         u.Diff(y).Diff(x), u.Diff(y).Diff(y)), 
        dims=(2,2)
    )

#VEC = H1(mesh, order=3, dirichlet=".*", dim=2)
VEC = H1(mesh, order=1, dim = 2)
X, PHI = VEC.TnT()

dJOmega = LinearForm(VEC)
dJOmega += InnerProduct((div(PHI)*(grad(gfu)- grad_ud)), grad(gfu)- grad_ud) * dx
dJOmega += -2* InnerProduct(hesse(ud)*PHI, grad(gfu)- grad_ud) * dx
dJOmega += div(PHI)* gfu *gfp *dx
dJOmega += InnerProduct(div(PHI)*grad(gfu), grad(gfp)) * dx
dJOmega += -InnerProduct(PHI.Deriv()*grad(gfu), grad(gfp)) * dx
dJOmega += -InnerProduct(grad(gfu), PHI.Deriv()*grad(gfp)) * dx
dJOmega += -div(PHI)* f * gfp * dx
dJOmega += -grad_f * PHI*gfp * dx
# added volumen constraint
dJOmega += -vol * div(PHI)* dx 


In [10]:
def pose_deformation_equation(gamma=None, p = None): 
    b = BilinearForm(VEC)
    # standard case
    if not p:
        b += InnerProduct(grad(X),grad(PHI))*dx + InnerProduct(X,PHI)*dx

    if gamma:
        # standard case with gamma regularization
        print('Using gamma =', gamma)
        b = BilinearForm(VEC)
        b += (1.0/gamma)*InnerProduct(grad(X),grad(PHI))*dx + (1.0/gamma)*InnerProduct(X,PHI)*dx
    

        b += gamma * (PHI.Deriv()[0,0] - PHI.Deriv()[1,1])*(X.Deriv()[0,0] - X.Deriv()[1,1]) *dx
        b += gamma * (PHI.Deriv()[1,0] + PHI.Deriv()[0,1])*(X.Deriv()[1,0] + X.Deriv()[0,1]) *dx


        #print("expression tree\n")
        #print(b)
        return b
    
    elif p:
        
        # solving minimization problem
        print('Using p =', p)
        eps = 1E-5
    
        grad_norm = sqrt(InnerProduct(grad(X), grad(X)) + eps**2)
        

        c = BilinearForm(VEC)
        c += (grad_norm**(p-2)) * InnerProduct(grad(X), grad(PHI)) * dx
        c += InnerProduct(X,PHI)*dx
        
        # -DJ(Omega)(PHI)
        c += -InnerProduct((div(PHI)*(grad(gfu)- grad_ud)), grad(gfu)- grad_ud) * dx
        c += 2* InnerProduct(grad(gfu)- grad_ud, hesse(ud)*PHI) * dx
        c += -div(PHI)* gfu *gfp *dx
        c += -InnerProduct(div(PHI)*grad(gfu), grad(gfp)) * dx
        c += InnerProduct(PHI.Deriv()*grad(gfu), grad(gfp)) * dx
        c += InnerProduct(grad(gfu), PHI.Deriv()*grad(gfp)) * dx
        c += div(PHI)* f * gfp * dx
        c += grad_f*PHI*gfp * dx
        c += vol * div(PHI)*dx 
        
        # c += -div(PHI)* f * gfp * dx
        # c += -grad_f*PHI*gfp * dx
        
        return c

        
    #print("expression tree\n")
    #print(b)
    return b
   

def SolveDeformationEquation(linear=True):
    if linear:
        #print("solving linear deformation equation")
        rhs = gfX.vec.CreateVector()
        rhs.data = dJOmega.vec - b.mat * gfX.vec
        update = gfX.vec.CreateVector()
        update.data = b.mat.Inverse(VEC.FreeDofs()) * rhs
        gfX.vec.data += update
        #scene_gfset.Redraw()
   
    elif not linear:
        #print("solving nonlinear deformation equation with Newton")
        Newton(c, gfX, maxerr = 1E-8, freedofs=VEC.FreeDofs(), maxit = 1000, printing=True)

        #print("Deformation norm:", Norm(gfX.vec)
        #scene_gfset.Redraw()
        


In [11]:
def check_mesh_quality():
    h = specialcf.mesh_size
    gf_h = GridFunction(L2(mesh, order=0))
    gf_h.Set(h)

    qual = gf_h.vec.FV().NumPy()
    qual /= maxH
    
    print("=================Mesh Quality Check=================")
    print("max quality:", np.max(qual), " min quality:", np.min(qual), " mean quality:", np.mean(qual))
    print("===================================================")
 
    #return Integrate(h, mesh, element_wise=True)



In [12]:
def optimize_shape(linear = True, LineSearch = True):
    gfset.Set((0,0))
    mesh.SetDeformation(gfset)
    scene.Redraw()
    a.Assemble()
    fstate.Assemble()
    SolveStateEquation()


    iter_max = 600
    Jold = Integrate(Cost(gfu), mesh)
    converged = False

    # input("Press enter to start optimization")
    print('Cost at initial design', Integrate (Cost(gfu), mesh))
    for k in range(iter_max):
        mesh.SetDeformation(gfset)
        scene.Redraw()

        print('cost at iteration', k, ': ', Jold)

        a.Assemble()
        fstate.Assemble()
        SolveStateEquation()

        fadjoint.Assemble()
        SolveAdjointEquation()
        if linear:
            b.Assemble()
        #plt.spy(b.mat.ToDense())
        dJOmega.Assemble()
        SolveDeformationEquation(linear=linear)

        #scale = 0.01 / Norm(gfX.vec)
        
        scale = 1E-4

        gfsetOld.vec[:] = gfset.vec[:]
        gfset.vec.data -= scale * gfX.vec

        Jnew = Integrate(Cost(gfu), mesh)
        if not LineSearch:
            if Jnew >= Jold:
                print("No descent found for current step size")
                converged = True

        #print("gradient norm", np.linalg.norm(dJOmega.vec.FV().NumPy()))
        if LineSearch:
            while Jnew > Jold and scale > 1e-12:
                #input('a')
                scale = min(1E-3, scale/2)
                print("scale = ", scale)
                #print("scale without normalization factor = ", scale* Norm(gfX.vec))
                if scale <= 1e-12:
                    converged = True
                    break

                gfset.vec.data = gfsetOld.vec - scale * gfX.vec         # scale times -X is descent direction
                mesh.SetDeformation(gfset)                              # applying deformation and solve new state

                a.Assemble()                                           # note that during line search we only have to solve state to check if update yields lower costs              
                fstate.Assemble()
                SolveStateEquation()
                Jnew = Integrate(Cost(gfu), mesh)
                print("New cost during line search: ", Jnew)
        
        #print("scaling parameter:", scale)
        #print("descet direction value", -1*np.dot(dJOmega.vec.FV().NumPy(), gfX.vec.FV().NumPy()))

        if converged==True:
            print("No more descent can be found")
            break
        Jold = Jnew

        Redraw(blocking=True)

    #print("Norm of gset", Integrate(gfset**2, mesh))

In [13]:
a1 = check_mesh_quality()
gfX = GridFunction(VEC)
b = pose_deformation_equation()

gfset = GridFunction(VEC)
gfset.Set((0,0))
gfsetOld = GridFunction(VEC)

scene = Draw(gfset,mesh,"gfset")
SetVisualization (deformation=True)



optimize_shape(linear = True)
mesh.SetDeformation(gfset)

a2 = check_mesh_quality()

# gfX2 = GridFunction(VEC)
# gfX2.vec.data =
# print("=====")
# print(np.dot(dJOmega.vec.FV().NumPy(), gfX.vec.FV().NumPy()))
# print(Integrate(Cost(gfu), mesh))


=================Mesh Quality Check=================
max quality: 1.452321790073649  min quality: 0.5768477774464785  mean quality: 0.8831324760843785


WebGuiWidget(layout=Layout(height='50vh', width='100%'), value={'gui_settings': {}, 'ngsolve_version': '6.2.24…

Cost at initial design 13.96238810275433
cost at iteration 0 :  13.96238810275433
cost at iteration 1 :  13.735550739621843
cost at iteration 2 :  13.526642840331323


cost at iteration 3 :  13.322392417508466


cost at iteration 4 :  13.12265849375249
cost at iteration 5 :  12.927305689331154
cost at iteration 6 :  12.736203943744316


...

scale =  5e-05
New cost during line search:  1.242616032021647
cost at iteration 480 :  1.242616032021647
scale =  5e-05
New cost during line search:  1.2426156656099823
cost at iteration 481 :  1.2426156656099823
scale =  5e-05


New cost during line search:  1.242617568717261
scale =  2.5e-05
New cost during line search:  1.2426165396036053
scale =  1.25e-05
New cost during line search:  1.2426160832181463
scale =  6.25e-06


New cost during line search:  1.2426158695670388
scale =  3.125e-06
New cost during line search:  1.24261576637678
scale =  1.5625e-06
New cost during line search:  1.2426157156904207
scale =  7.8125e-07
New cost during line search:  1.2426156905745076
scale =  3.90625e-07
New cost during line search:  1.242615678073288
scale =  1.953125e-07
New cost during line search:  1.2426156718368953
scale =  9.765625e-08
New cost during line search:  1.2426156687222547
scale =  4.8828125e-08
New cost during line search:  1.2426156671658437
scale =  2.44140625e-08
New cost during line search:  1.242615666387826
scale =  1.220703125e-08
New cost during line search:  1.2426156659988907
scale =  6.103515625e-09
New cost during line search:  1.2426156658044298
scale =  3.0517578125e-09


New cost during line search:  1.2426156657071838
scale =  1.52587890625e-09
New cost during line search:  1.2426156656586058
scale =  7.62939453125e-10
New cost during line search:  1.242615665634289
scale =  3.814697265625e-10


New cost during line search:  1.242615665622116
scale =  1.9073486328125e-10
New cost during line search:  1.2426156656160388
scale =  9.5367431640625e-11
New cost during line search:  1.2426156656130096
scale =  4.76837158203125e-11
New cost during line search:  1.2426156656114715
scale =  2.384185791015625e-11
New cost during line search:  1.2426156656107425
scale =  1.1920928955078126e-11
New cost during line search:  1.2426156656103344
scale =  5.960464477539063e-12
New cost during line search:  1.2426156656101475
scale =  2.9802322387695314e-12
New cost during line search:  1.2426156656100888
scale =  1.4901161193847657e-12
New cost during line search:  1.2426156656099985
scale =  7.450580596923828e-13
No more descent can be found
=================Mesh Quality Check=================
max quality: 1.4420554859725245  min quality: 0.5166402075400832  mean quality: 0.8593656411107816


In [14]:
check_mesh_quality()
gfX = GridFunction(VEC)

b = pose_deformation_equation(gamma=1)

gfset = GridFunction(VEC)
gfset.Set((0,0))
gfsetOld = GridFunction(VEC)

scene = Draw(gfset,mesh,"gfset")
SetVisualization (deformation=True)

optimize_shape(linear = True)

mesh.SetDeformation(gfset)
check_mesh_quality()


=================Mesh Quality Check=================
max quality: 1.4420554859725245  min quality: 0.5166402075400832  mean quality: 0.8593656411107816
Using gamma = 1


WebGuiWidget(layout=Layout(height='50vh', width='100%'), value={'gui_settings': {}, 'ngsolve_version': '6.2.24…

Cost at initial design 13.962388102754325
cost at iteration 0 :  13.962388102754325


cost at iteration 1 :  13.825772613698412
cost at iteration 2 :  13.708401589313848


cost at iteration 3 :  13.592734781168076


...

cost at iteration 591 :  1.4516167023670545
cost at iteration 592 :  1.4491501236004325


cost at iteration 593 :  1.4466942866372101
cost at iteration 594 :  1.4442491442645735


cost at iteration 595 :  1.4418146495442976
cost at iteration 596 :  1.4393907558107133


cost at iteration 597 :  1.436977416668975
cost at iteration 598 :  1.4345745859929717


cost at iteration 599 :  1.4321822179235317
=================Mesh Quality Check=================
max quality: 1.1832106186704068  min quality: 0.5059467464043369  mean quality: 0.8036611401632984


In [15]:
check_mesh_quality()
c = pose_deformation_equation(p=2)

gfX = GridFunction(VEC)
gfX.Set((x *(1-x)*y*(1-y),0))

gfsetOld = GridFunction(VEC)
gfset = GridFunction(VEC)
gfset.Set((0,0))

scene = Draw(gfset,mesh,"gfset")
SetVisualization (deformation=True)


optimize_shape(linear=False)
mesh.SetDeformation(gfset)
check_mesh_quality()

=================Mesh Quality Check=================
max quality: 1.1832106186704068  min quality: 0.5059467464043369  mean quality: 0.8036611401632984
Using p = 2


WebGuiWidget(layout=Layout(height='50vh', width='100%'), value={'gui_settings': {}, 'ngsolve_version': '6.2.24…

Cost at initial design 13.962388102754339
cost at iteration 0 :  13.962388102754339
Newton iteration  0
err =  37.410916722694864
Newton iteration  1


err =  1.8869214813442775e-13
cost at iteration 1 :  13.735607075299352
Newton iteration  0


err =  0.5046122613881028
Newton iteration  1


...

err =  0.003011349663225307
Newton iteration  1
err =  5.3918315175923764e-15
scale =  5e-05


New cost during line search:  1.244164165163216
scale =  2.5e-05
New cost during line search:  1.2441634989728694
scale =  1.25e-05
New cost during line search:  1.2441632245647072
scale =  6.25e-06
New cost during line search:  1.244163102031241
scale =  3.125e-06
New cost during line search:  1.2441630444319927
scale =  1.5625e-06
New cost during line search:  1.2441630165492428
scale =  7.8125e-07
New cost during line search:  1.2441630028370567
scale =  3.90625e-07
New cost during line search:  1.244162996038274
scale =  1.953125e-07
New cost during line search:  1.2441629926532174
scale =  9.765625e-08
New cost during line search:  1.2441629909642733
scale =  4.8828125e-08
New cost during line search:  1.2441629901206601
scale =  2.44140625e-08


New cost during line search:  1.24416298969912
scale =  1.220703125e-08
New cost during line search:  1.2441629894884019
scale =  6.103515625e-09
New cost during line search:  1.2441629893830144
scale =  3.0517578125e-09


New cost during line search:  1.2441629893303696
scale =  1.52587890625e-09
New cost during line search:  1.244162989304043
scale =  7.62939453125e-10
New cost during line search:  1.2441629892908286
scale =  3.814697265625e-10
New cost during line search:  1.2441629892842996
scale =  1.9073486328125e-10
New cost during line search:  1.2441629892809771
scale =  9.5367431640625e-11
New cost during line search:  1.2441629892793518
scale =  4.76837158203125e-11
New cost during line search:  1.2441629892785286
scale =  2.384185791015625e-11
New cost during line search:  1.2441629892780874
scale =  1.1920928955078126e-11
New cost during line search:  1.2441629892778983
scale =  5.960464477539063e-12
New cost during line search:  1.2441629892777857
scale =  2.9802322387695314e-12
New cost during line search:  1.2441629892777466
scale =  1.4901161193847657e-12


New cost during line search:  1.2441629892777295
scale =  7.450580596923828e-13
No more descent can be found
=================Mesh Quality Check=================
max quality: 1.441807871875525  min quality: 0.5167710698008765  mean quality: 0.8594784827643153


In [16]:
check_mesh_quality()
c = pose_deformation_equation(p=5)

gfX = GridFunction(VEC)
gfX.Set((x *(1-x)*y*(1-y),0))

gfset = GridFunction(VEC)
gfsetOld = GridFunction(VEC)
gfset.Set((0,0))

scene = Draw(gfset,mesh,"gfset")
SetVisualization (deformation=True)

optimize_shape(linear=False)
mesh.SetDeformation(gfset)
check_mesh_quality()

=================Mesh Quality Check=================
max quality: 1.441807871875525  min quality: 0.5167710698008765  mean quality: 0.8594784827643153
Using p = 5


WebGuiWidget(layout=Layout(height='50vh', width='100%'), value={'gui_settings': {}, 'ngsolve_version': '6.2.24…

Cost at initial design 13.962388102754325
cost at iteration 0 :  13.962388102754325
Newton iteration  0
err =  69.38374121332043
Newton iteration  1
err =  95525973.66348527
Newton iteration  2
err =  46534454.951519154
Newton iteration  3


err =  22668761.32833453
Newton iteration  4
err =  11042844.290232865
Newton iteration  5


err =  5379403.322999564
Newton iteration  6
err =  2620518.71335221
Newton iteration  7
err =  1276557.6244199935
Newton iteration  8
err =  621861.3742348586
Newton iteration  9
err =  302933.1079457248
Newton iteration  10


...

err =  1.8333207316496864e-09
cost at iteration 597 :  5.176887927187565


Newton iteration  0
err =  0.007691243072542982
Newton iteration  1
err =  2.1460882818521602e-05
Newton iteration  2
err =  1.8944752194511004e-09
cost at iteration 598 :  5.168652560466924
Newton iteration  0


err =  0.007688546557093541
Newton iteration  1


err =  2.1720254346073952e-05
Newton iteration  2
err =  1.9549982557593685e-09
cost at iteration 599 :  5.160432037078894
Newton iteration  0
err =  0.007685947485827505
Newton iteration  1
err =  2.1975093732839245e-05
Newton iteration  2


err =  2.014337234123511e-09
=================Mesh Quality Check=================
max quality: 1.37841365416341  min quality: 0.5553651552984573  mean quality: 0.858318409251656
